In [43]:
import numpy as np
import pandas as pd
import time
import warnings
warnings.simplefilter("ignore")
from joblib import load
import shap
shap.initjs()
from sklearn.ensemble import VotingClassifier
import os
import matplotlib.pyplot as plt

In [2]:
var = 'snv_protein_coding'
X_train = pd.read_csv(f'{var}/train_{var}/merged_data-train_{var}.csv')
#var = X_train[config_dict['ML_VAR']]
X_train = X_train.drop(['SYMBOL','Feature','Consequence','clinvar_CLNREVSTAT','clinvar_CLNSIG','Alternate Allele','Reference Allele','ID'], axis=1)
#feature_names = X_train.columns.tolist()
X_train = X_train.values
#Y_train = pd.read_csv(f'{var}/train_{var}/merged_data-y-train_{var}.csv')
#Y_train = label_binarize(Y_train.values, classes=['low_impact', 'high_impact']).ravel() 

x_test = pd.read_csv(f'{var}/test_{var}/merged_data-test_{var}.csv')
x_test = x_test.drop(['SYMBOL','Feature','Consequence','clinvar_CLNREVSTAT','clinvar_CLNSIG','Alternate Allele','Reference Allele','ID'], axis=1)
feature_names = X_test.columns.tolist()
X_test = x_test.values
Y_test = pd.read_csv(f'{var}/test_{var}/merged_data-y-test_{var}.csv')
print('Data Loaded!')
#Y = pd.get_dummies(y)
#Y_test = label_binarize(Y_test.values, classes=['low_impact', 'high_impact']).ravel() 
print(f'Shape: {Y_test.shape}')
#scaler = StandardScaler().fit(X_train)
#X_train = scaler.transform(X_train)
#X_test = scaler.transform(X_test)
# explain all the predictions in the test set
background = shap.kmeans(X_train, 10)

Data Loaded!
Shape: (1694301, 1)


In [58]:
feature_names = x_test.columns.tolist()

In [3]:
with open(f"./{var}/VotingClassifier_{var}.joblib", 'rb') as f:
    clf = load(f)

In [12]:
x_test[1:2]

SIFT  PolyPhen  CADD_PHRED  FATHMM_score  MutationAssessor_score  \
1  0.01     0.014        21.9           0.0             1819.545455   

   PROVEAN_score  VEST4_score    GERP  MutationTaster_score  DANN_score  ...  \
1    -553.727273   208.909091  4012.0              989169.0     0.98576  ...   

   BIOTYPE_lncRNA  BIOTYPE_miRNA  BIOTYPE_misc_RNA  BIOTYPE_ncRNA_pseudogene  \
1               0              0                 0                         0   

   BIOTYPE_protein_coding  BIOTYPE_scRNA  BIOTYPE_snRNA  BIOTYPE_snoRNA  \
1                     1.0              0              0               0   

   BIOTYPE_telomerase_RNA  BIOTYPE_transcribed_pseudogene  
1                       0                               0  

[1 rows x 78 columns]

In [64]:
Y_test[0:1]

hgmd_class
0  high_impact

In [32]:
explainer = shap.KernelExplainer(clf.predict_proba, background)

In [51]:
#For 1000 random variants all at once
background = X_test[np.random.choice(X_test.shape[0], 1000, replace=False)]
shap_values = explainer.shap_values(background)

In [59]:
shap.force_plot(explainer.expected_value[1], shap_values[1], background, feature_names)

In [65]:
#For 1 variant
shap_values = explainer.shap_values(x_test.iloc[0,:])
shap.force_plot(explainer.expected_value[1], shap_values[1], x_test.iloc[0,:])